In [2]:
import sys
import json
import pickle
import numpy as np
import pandas as pd
import googlemaps as gmaps

from os import listdir, walk
from tqdm import tqdm
from pathlib import Path
from datetime import datetime
from datatable import dt, f, by

from plotly import express as px, io as pio
pd.options.plotting.backend = 'plotly'
pio.renderers.default = 'plotly_mimetype+notebook_connected'

from utils import get_path, data_load
sys.path.insert(0, '../')
from secret import API_KEY

# Descrição

Get the travel distance and time for a matrix of origins and destinations.

[Documentação](https://developers.google.com/maps/documentation/distance-matrix/start#maps_http_distancematrix_start-py)

[Repositório API Python](https://github.com/googlemaps/google-maps-services-python)

# Fontes de dados

## Municípios

### Carregando tabela

In [42]:
path_munic = get_path('LOCALIDADES', 'municipios.csv.gzip')
df_munic = dt.fread(path_munic)
df_munic

<Frame#7fd2b0094540 5570x9>

## SIH

### Colunas

In [43]:
cols_sih = {
  'cod_municipio': 'origem',
  'hosp_cod_municipio': 'destino',
}

### Carregando tabela

In [44]:
path_sih = get_path('SIH', 'sih.jay')
df_sih = dt.fread(path_sih, columns=cols_sih)
df_sih.names = cols_sih
df_sih = df_sih[:, list(cols_sih.values())]
df_sih = df_sih[f.origem != f.destino, :]
df_sih['count'] = 1
df_sih = df_sih[:, dt.sum(f.count), by('origem', 'destino')]
df_sih = df_sih.sort(-f.count)
df_sih

<Frame#7fd309b173f0 68573x3>

# Adicinar colunas

## Latitude & Longitude

In [45]:
def get_latlon_table_by_ref(df_munic, ref):
  cols_latlon = ['cod_municipio', 'latitude', 'longitude']
  df_latlon = df_munic[:, cols_latlon]
  df_latlon.names = {
    'cod_municipio': ref,
    'latitude': f'{ref}_latitude',
    'longitude': f'{ref}_longitude',
  }
  df_latlon.key = ref
  return df_latlon

## Parâmetros

In [46]:
def params_in_cols(df):
  dfs = list()
  for mode in ['driving', 'transit']: # driving | transit | bicycling | walking
    for hour in [6, 12, 18]: # [6, 12, 18] | [7, 13, 19]
      for traffic_model in ['best_guess', 'optimistic', 'pessimistic']: # best_guess | optimistic | pessimistic
        if mode != 'driving' and traffic_model != 'best_guess':
          continue
        df_ = df.copy()
        df_['mode'] = mode
        df_['traffic_model'] = traffic_model
        df_['hour'] = hour
        dfs.append(df_)
  df_param = pd.concat(dfs)
  df_param = df_param.sort_values(by=[
    'origem', 'destino', 'mode', 'traffic_model', 'hour'])
  df_param = df_param.reset_index(drop=True)
  return df_param

# Modelo de Coleta

## Local pra armazenar arquivo

In [47]:
def get_backup_path(data):
  infos = [
    f'{data["hour"]}h',
    data['mode'],
    data['traffic_model'],
    str(data['origem']),
    str(data['destino'])]
  fname = '-'.join(infos)
  dir = '/'.join(infos[:-1])
  path_dir = get_path('LOCALIDADES', f'google_maps/{dir}')
  Path(path_dir).mkdir(parents=True, exist_ok=True)
  return path_dir + f'/{fname}.json'

## Requisição para API

In [48]:
def get_travel_info(row):
  departure_time = datetime(year=2022, month=11, day=7, hour=row['hour'])
  info = row.copy()
  info['departure_time'] = str(departure_time)
  res = gmaps.distance_matrix(
    origins = [(row['origem_latitude'], row['origem_longitude'])],
    destinations = [(row['destino_latitude'], row['destino_longitude'])],
    mode = row['mode'],
    traffic_model = row['traffic_model'],
    departure_time = departure_time,
    language = 'pt-BR',
    units = 'metric',)
  info['origin_addresses'] = res['origin_addresses'][0]
  info['destination_addresses'] = res['destination_addresses'][0]
  elem = res['rows'][0]['elements'][0]
  info['status'] = elem['status']
  for col in list(elem):
    if col == 'status':
      continue
    for i_type in ['text', 'value']:
      col_name = f'{col} ({i_type})'
      if elem['status'] == 'OK':
        info[col_name] = elem[col][i_type]
      else:
        info[col_name] = ''
  return info

## Coleta das informações

In [49]:
def request_travel_infos(df):
  for row in tqdm(df.to_dict(orient='records')):
    fpath = get_backup_path(row)
    if Path(fpath).is_file() or (row['origem'] == row['destino']):
      continue
    try:
      info = get_travel_info(row)
    except:
      info = {'status': 'ApiError'}
    with open(fpath, 'w') as fp:
      json.dump(info, fp)

# Gerando tabela

Tabela com informações a serem enviadas para a API do Google Maps.

In [100]:
df_latlon_orig = get_latlon_table_by_ref(df_munic, 'origem')
df_latlon_dest = get_latlon_table_by_ref(df_munic, 'destino')
df_route = df_sih[:, :, dt.join(df_latlon_orig)]
df_route = df_route[:, :, dt.join(df_latlon_dest)]
df_route = params_in_cols(df_route.to_pandas())
df_route

origem  destino  count  origem_latitude  origem_longitude  \
0       110001   110002      2         -11.9283          -61.9953   
1       110001   110002      2         -11.9283          -61.9953   
2       110001   110002      2         -11.9283          -61.9953   
3       110001   110002      2         -11.9283          -61.9953   
4       110001   110002      2         -11.9283          -61.9953   
...        ...      ...    ...              ...               ...   
822871  530010   522200      2         -15.7795          -47.9297   
822872  530010   522200      2         -15.7795          -47.9297   
822873  530010   522200      2         -15.7795          -47.9297   
822874  530010   522200      2         -15.7795          -47.9297   
822875  530010   522200      2         -15.7795          -47.9297   

        destino_latitude  destino_longitude     mode traffic_model  hour  
0               -9.90571           -63.0325  driving    best_guess     6  
1               -9.90571           -63.0325  driving    best_guess    12  
2               -9.90571           -63.0325  driving    best_guess    18  
3               -9.90571           -63.0325  driving    optimistic     6  
4               -9.90571           -63.0325  driving    optimistic    12  
...                  ...                ...      ...           ...   ...  
822871         -16.74050           -48.5159  driving   pessimistic    12  
822872         -16.74050           -48.5159  driving   pessimistic    18  
822873         -16.74050           -48.5159  transit    best_guess     6  
822874         -16.74050           -48.5159  transit    best_guess    12  
822875         -16.74050           -48.5159  transit    best_guess    18  

[822876 rows x 10 columns]

In [ ]:
df_route_sorted = df_route.sort_values('count', ascending=False)
df_route_sorted

origem  destino  count  origem_latitude  origem_longitude  \
786107  510840   510340  22807        -15.64580          -56.1322   
786106  510840   510340  22807        -15.64580          -56.1322   
786105  510840   510340  22807        -15.64580          -56.1322   
786104  510840   510340  22807        -15.64580          -56.1322   
786103  510840   510340  22807        -15.64580          -56.1322   
...        ...      ...    ...              ...               ...   
247865  260730   270430      1         -7.64505          -40.1476   
247866  260730   270430      1         -7.64505          -40.1476   
247867  260730   270430      1         -7.64505          -40.1476   
247868  260730   270430      1         -7.64505          -40.1476   
608604  355220   130260      1        -23.49690          -47.4451   

        destino_latitude  destino_longitude     mode traffic_model  hour  
786107         -15.60100           -56.0974  transit    best_guess    18  
786106         -15.60100           -56.0974  transit    best_guess    12  
786105         -15.60100           -56.0974  transit    best_guess     6  
786104         -15.60100           -56.0974  driving   pessimistic    18  
786103         -15.60100           -56.0974  driving   pessimistic    12  
...                  ...                ...      ...           ...   ...  
247865          -9.66599           -35.7350  driving    optimistic    18  
247866          -9.66599           -35.7350  driving   pessimistic     6  
247867          -9.66599           -35.7350  driving   pessimistic    12  
247868          -9.66599           -35.7350  driving   pessimistic    18  
608604          -3.11866           -60.0212  driving    best_guess     6  

[822876 rows x 10 columns]

# Coleta dos dados

## Seleção parâmetros

In [ ]:
def select_params(
    df,
    mode, # driving | transit | bicycling | walking
    traffic_model, # best_guess | optimistic | pessimistic
    hour, # [6, 12, 18] | [7, 13, 19]
  ):
  df_param = df[
    (
      df['mode'] == mode
    ) & (
      df['traffic_model'] == traffic_model
    ) & (
      df['hour'] == hour
    )
  ].sort_values(by='count', ascending=False)
  return df_param

## Filtros

### Intra RJ

`origem` e `destino` no estado do RJ.

In [ ]:
origem_rj = df_route['origem'].astype(str).str.startswith('33')
destino_rj = df_route['destino'].astype(str).str.startswith('33')
df_route_rj = df_route[origem_rj & destino_rj]
df_route_rj

origem  destino  count  origem_latitude  origem_longitude  \
497964  330010   330023      1         -23.0011          -44.3196   
497965  330010   330023      1         -23.0011          -44.3196   
497966  330010   330023      1         -23.0011          -44.3196   
497967  330010   330023      1         -23.0011          -44.3196   
497968  330010   330023      1         -23.0011          -44.3196   
...        ...      ...    ...              ...               ...   
519643  330630   330620      1         -22.5202          -44.0996   
519644  330630   330620      1         -22.5202          -44.0996   
519645  330630   330620      1         -22.5202          -44.0996   
519646  330630   330620      1         -22.5202          -44.0996   
519647  330630   330620      1         -22.5202          -44.0996   

        destino_latitude  destino_longitude     mode traffic_model  hour  
497964          -22.7528           -41.8846  driving    best_guess     6  
497965          -22.7528           -41.8846  driving    best_guess    12  
497966          -22.7528           -41.8846  driving    best_guess    18  
497967          -22.7528           -41.8846  driving    optimistic     6  
497968          -22.7528           -41.8846  driving    optimistic    12  
...                  ...                ...      ...           ...   ...  
519643          -22.4059           -43.6686  driving   pessimistic    12  
519644          -22.4059           -43.6686  driving   pessimistic    18  
519645          -22.4059           -43.6686  transit    best_guess     6  
519646          -22.4059           -43.6686  transit    best_guess    12  
519647          -22.4059           -43.6686  transit    best_guess    18  

[15792 rows x 10 columns]

## Consulta API

In [ ]:
gmaps = gmaps.Client(key=API_KEY)

In [ ]:
# df_param = select_params(df_route_rj, 'driving', 'pessimistic', 18)
# df_param = select_params(df_route_rj, 'transit', 'best_guess', 6)
# df_param

In [ ]:
# df_param = select_params(df_route_sorted, 'driving', 'pessimistic', 18)
# request_travel_infos(df_param)

In [ ]:
# df_param = select_params(df_route_sorted, 'transit', 'best_guess', 6)
# request_travel_infos(df_param)

RJ driving best_guess 6h

100%|██████████| 1316/1316 [04:07<00:00,  5.32it/s]

RJ driving best_guess 12h

100%|██████████| 1316/1316 [04:28<00:00,  4.91it/s]

RJ driving best_guess 18h

100%|██████████| 1316/1316 [04:29<00:00,  4.89it/s]

RJ driving pessimistic 18h

100%|██████████| 1316/1316 [04:26<00:00,  5.12it/s]

RJ transit best_guess 12h

100%|██████████| 1316/1316 [03:20<00:00,  6.56it/s]

# Resultado da coleta

## Lendo arquivos salvos

In [4]:
def read_data_to_df(path_dir, cols_order=None):
  files = list()
  for (dirpath, _, filenames) in walk(path_dir):
    files.extend([dirpath + '/' + fl for fl in filenames if 'json' in fl])
  infos = list()
  for file in files:
    with open(file) as fl:
      d = json.load(fl)
      infos.append(d)
  df = pd.DataFrame(infos)
  cols_order = df.columns if cols_order is None else cols_order
  return df[cols_order]

## Ordenando colunas

In [5]:
cols_order = [
  'status', 'origem', 'destino', 'origin_addresses', 'destination_addresses',
  'origem_latitude', 'origem_longitude', 'destino_latitude', 'destino_longitude',
  'hour', 'departure_time', 'mode', 'traffic_model',
  'distance (value)', 'distance (text)',
  'duration (value)', 'duration (text)',
  'duration_in_traffic (value)', 'duration_in_traffic (text)',
  'count',
]

## Tabela resultante

In [6]:
path_gmaps = get_path('LOCALIDADES', f'google_maps/')
path_routes = get_path('GESTANTES', f'gmaps/routes.csv.gzip')
df_files = read_data_to_df(path_gmaps, cols_order=cols_order)
# df_files = pd.read_csv(path_routes)
df_files

status    origem   destino  \
0      ZERO_RESULTS  292070.0  291360.0   
1      ZERO_RESULTS  290515.0  293330.0   
2                OK  330330.0  330490.0   
3                OK  330330.0  330185.0   
4                OK  330330.0  330023.0   
...             ...       ...       ...   
65933            OK  291810.0  280290.0   
65934            OK  431075.0  431310.0   
65935            OK  431075.0  431490.0   
65936            OK  431075.0  431690.0   
65937            OK  431849.0  432180.0   

                                        origin_addresses  \
0                                      -14.1035,-39.0137   
1                                      -14.3347,-40.9175   
2      R. Maria Bregua, 37 - São Lourenço, Niterói - ...   
3      R. Maria Bregua, 37 - São Lourenço, Niterói - ...   
4      R. Maria Bregua, 37 - São Lourenço, Niterói - ...   
...                                                  ...   
65933  R. Delmiro Gouveia, 109 - Centro, Jeremoabo - ...   
65934  Av. Gen. Osório, 20, Ivorá - RS, 98160-000, Br...   
65935  Av. Gen. Osório, 20, Ivorá - RS, 98160-000, Br...   
65936  Av. Gen. Osório, 20, Ivorá - RS, 98160-000, Br...   
65937  Rua Linha da Barra Zona Rural, São José do Inh...   

                                   destination_addresses  origem_latitude  \
0                                        -14.793,-39.046         -14.1035   
1                                      -14.8615,-40.8442         -14.3347   
2      R. Temistocles de Almeida, 134 - Camarão, São ...         -22.8832   
3      R. João da Silva Maia, 14 - Parque Santo Anton...         -22.8832   
4      Av. José Bento Ribeiro Dantas, 842, Búzios - R...         -22.8832   
...                                                  ...              ...   
65933  R. Cap. José Ferreira Neto, 244 - Centro, Itab...         -10.0685   
65934  R. Raimundo Aléssio, 325 - Nova Palma, RS, 972...         -29.5232   
65935  R. Casemiro de Abreu, 193 - Boa Vista, Porto A...         -29.5232   
65936  R. Conde de Porto Alegre, 365 - Bonfim, Santa ...         -29.5232   
65937  R. Padre Cacique, 692 - Centro, Três de Maio -...         -27.7251   

       origem_longitude  destino_latitude  destino_longitude  hour  \
0              -39.0137          -14.7930           -39.0460   6.0   
1              -40.9175          -14.8615           -40.8442   6.0   
2              -43.1034          -22.8268           -43.0634   6.0   
3              -43.1034          -22.5347           -42.9895   6.0   
4              -43.1034          -22.7528           -41.8846   6.0   
...                 ...               ...                ...   ...   
65933          -38.3471          -10.6826           -37.4273  18.0   
65934          -53.5842          -29.4710           -53.4689  18.0   
65935          -53.5842          -30.0318           -51.2065  18.0   
65936          -53.5842          -29.6868           -53.8149  18.0   
65937          -54.1275          -27.7800           -54.2357  18.0   

            departure_time     mode traffic_model  distance (value)  \
0      2022-11-07 06:00:00  transit    best_guess               NaN   
1      2022-11-07 06:00:00  transit    best_guess               NaN   
2      2022-11-07 06:00:00  transit    best_guess            9900.0   
3      2022-11-07 06:00:00  transit    best_guess           63545.0   
4      2022-11-07 06:00:00  transit    best_guess          171243.0   
...                    ...      ...           ...               ...   
65933  2022-11-07 18:00:00  driving   pessimistic          144835.0   
65934  2022-11-07 18:00:00  driving   pessimistic           19878.0   
65935  2022-11-07 18:00:00  driving   pessimistic          285093.0   
65936  2022-11-07 18:00:00  driving   pessimistic           48429.0   
65937  2022-11-07 18:00:00  driving   pessimistic           19250.0   

      distance (text)  duration (value)     duration (text)  \
0                 NaN               NaN                 NaN   
1                 NaN         

In [ ]:
df_files['status'].value_counts()

OK              62991
ZERO_RESULTS     2943
ApiError            4
Name: status, dtype: int64

### Exportando

#### CSV

In [7]:
df_files.to_csv(path_routes, index=False)

#### XLSX

In [ ]:
# path_routes = get_path('GESTANTES', f'gmaps/routes.xlsx')
# df_files.to_excel(path_routes, index=False)

## 

# Investigação

In [ ]:
df_files.columns

Index(['status', 'origem', 'destino', 'origin_addresses',
       'destination_addresses', 'origem_latitude', 'origem_longitude',
       'destino_latitude', 'destino_longitude', 'hour', 'departure_time',
       'mode', 'traffic_model', 'distance (value)', 'distance (text)',
       'duration (value)', 'duration (text)', 'duration_in_traffic (value)',
       'duration_in_traffic (text)', 'count'],
      dtype='object')

In [ ]:
cols_inv = [
  'status', 'count',
  'origem', 'destino',
  'hour', 'mode', 'traffic_model',
  'distance (value)',
  'duration (value)', 'duration_in_traffic (value)',
]

In [ ]:
df_inv = df_files[cols_inv].sort_values(
  by=['origem', 'destino', 'hour', 'mode', 'traffic_model', 'distance (value)']
).reset_index(drop=True)
df_inv

status  count    origem   destino  hour     mode traffic_model  \
0            OK    2.0  110001.0  110002.0  18.0  driving   pessimistic   
1            OK   12.0  110001.0  110004.0  18.0  driving   pessimistic   
2            OK    2.0  110001.0  110009.0  18.0  driving   pessimistic   
3            OK   26.0  110001.0  110012.0  18.0  driving   pessimistic   
4            OK    3.0  110001.0  110013.0  18.0  driving   pessimistic   
...         ...    ...       ...       ...   ...      ...           ...   
65933        OK    2.0  530010.0  522200.0  18.0  driving   pessimistic   
65934  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65935  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65936  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65937  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   

       distance (value)  duration (value)  duration_in_traffic (value)  
0              330612.0           18065.0                      20190.0  
1              109937.0            6238.0                       6757.0  
2              143458.0            8228.0                      10193.0  
3              153453.0            8366.0                       9749.0  
4              389010.0           21686.0                      23707.0  
...                 ...               ...                          ...  
65933          163256.0            8350.0                      13232.0  
65934               NaN               NaN                          NaN  
65935               NaN               NaN                          NaN  
65936               NaN               NaN                          NaN  
65937               NaN               NaN                          NaN  

[65938 rows x 10 columns]

In [99]:
cols_route = ['origem', 'destino', 'distance (value)']
df_inv[cols_route].groupby(cols_route, as_index=False).sum()

origem   destino  distance (value)
0      110001.0  110002.0          330612.0
1      110001.0  110004.0          109937.0
2      110001.0  110009.0          143458.0
3      110001.0  110012.0          153453.0
4      110001.0  110013.0          389010.0
...         ...       ...               ...
59022  530010.0  521760.0           57271.0
59023  530010.0  521830.0          311269.0
59024  530010.0  521975.0           52771.0
59025  530010.0  522068.0          256309.0
59026  530010.0  522200.0          163256.0

[59027 rows x 3 columns]

## driving pessimistic in traffic at 6pm x transit at 12pm

### Consultar duração

In [ ]:
def get_duration(df, origem, destino, mode, traffic_model, hour, in_traffic=True):
  col_idx = int(in_traffic)
  col_duration = ['duration (value)', 'duration_in_traffic (value)'][col_idx]
  duration = df[
    (
      df['origem'] == origem
    ) & (
      df['destino'] == destino
    ) & (
      df['mode'] == mode
    ) & (
      df['traffic_model'] == traffic_model
    ) & (
      df['hour'] == hour
    )
  ]
  duration = list(duration[col_duration])[0]
  return duration

### Comparação

In [97]:
def hours_comparison(df):
  cols_route = ['origem', 'destino', 'distance (value)']
  df_select = df[(
      (df['mode'] == 'driving') & (df['traffic_model'] == 'pessimistic') & (df['hour'] == 18)
    ) | (
      (df['mode'] == 'transit') & (df['traffic_model'] == 'best_guess') & (df['hour'] == 6)
  )]
  for col in df_select.columns:
    if col not in {'status', 'mode', 'traffic_model', 'late_pct'}:
      df_select.loc[:, col] = df_select[col].apply(lambda x: x if pd.isna(x) else int(x))
  df_route = df_select[cols_route].groupby(cols_route, as_index=False).sum()
  ratios = list()
  for row in tqdm(df_route.to_dict(orient='records')):
    try:
      driving = get_duration(df_select, row['origem'], row['destino'], 'driving', 'pessimistic', 18, in_traffic=True)
      print(driving)
      transit = get_duration(df_select, row['origem'], row['destino'], 'transit', 'best_guess', 6, in_traffic=False)
      ratio = (transit - driving) / driving
    except:
      ratio = np.nan
    ratios.append(ratio)
  df_route['ratio'] = ratios
  df_route = df_route.sort_values(cols_route).reset_index(drop=True)
  return df_route#.dropna()

In [98]:
df_vs = hours_comparison(df_inv.dropna(subset=['duration (value)']))
df_vs

/var/folders/9d/972tfrtd01z2hhl836z97zdr0000gn/T/ipykernel_55860/3508088823.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/9d/972tfrtd01z2hhl836z97zdr0000gn/T/ipykernel_55860/3508088823.py:10: FutureWarning:

In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`

100%|██████████| 58352/58352 [00:00<00:00, 1364711.67it/s]


origem  destino  distance (value)  ratio
0      110001   110002            330612    NaN
1      110001   110004            109937    NaN
2      110001   110009            143458    NaN
3      110001   110012            153453    NaN
4      110001   110013            389010    NaN
...       ...      ...               ...    ...
58347  530010   521760             57271    NaN
58348  530010   521830            311269    NaN
58349  530010   521975             52771    NaN
58350  530010   522068            256309    NaN
58351  530010   522200            163256    NaN

[58352 rows x 4 columns]

### Histograma

In [ ]:
px.histogram(df_vs, x='ratio')

### Density contour

In [ ]:
fig = px.density_contour(df_vs, x='ratio', y='distance (value)', marginal_x="histogram", marginal_y="histogram") #log_x=True, log_y=True) # , opacity=.25
fig.show()

## % diferença com tráfego

### Tabela com atraso percentual

In [ ]:
traffic = 'duration_in_traffic (value)'
normal = 'duration (value)'
df_inv['late_pct'] = (df_inv[traffic] - df_inv[normal]) / df_inv[normal]
df_inv

status  count    origem   destino  hour     mode traffic_model  \
0            OK    2.0  110001.0  110002.0  18.0  driving   pessimistic   
1            OK   12.0  110001.0  110004.0  18.0  driving   pessimistic   
2            OK    2.0  110001.0  110009.0  18.0  driving   pessimistic   
3            OK   26.0  110001.0  110012.0  18.0  driving   pessimistic   
4            OK    3.0  110001.0  110013.0  18.0  driving   pessimistic   
...         ...    ...       ...       ...   ...      ...           ...   
65933        OK    2.0  530010.0  522200.0  18.0  driving   pessimistic   
65934  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65935  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65936  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65937  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   

       distance (value)  duration (value)  duration_in_traffic (value)  \
0              330612.0           18065.0                      20190.0   
1              109937.0            6238.0                       6757.0   
2              143458.0            8228.0                      10193.0   
3              153453.0            8366.0                       9749.0   
4              389010.0           21686.0                      23707.0   
...                 ...               ...                          ...   
65933          163256.0            8350.0                      13232.0   
65934               NaN               NaN                          NaN   
65935               NaN               NaN                          NaN   
65936               NaN               NaN                          NaN   
65937               NaN               NaN                          NaN   

       late_pct  
0      0.117631  
1      0.083200  
2      0.238819  
3      0.165312  
4      0.093194  
...         ...  
65933  0.584671  
65934       NaN  
65935       NaN  
65936       NaN  
65937       NaN  

[65938 rows x 11 columns]

### Histograma

`traffic = normal + normal * late_pct`

In [ ]:
px.histogram(df_inv, x='late_pct', color='hour', barmode='overlay', opacity=.5)

## Comparação entre horas

### Consultar duração

In [ ]:
def get_duration(df, origem, destino, hour, col):
  return list(df[
    (
      df['origem'] == origem
    ) & (
      df['destino'] == destino
    ) & (
      df['hour'] == hour
    )
  ][col])[0]

### Tabela de comparação entre horários

In [ ]:
def hours_comparison(df, i=0):
  cols_route = ['origem', 'destino']
  cols_duration = ['duration_in_traffic (value)', 'duration (value)']
  # hours = list(df_inv['hour'].unique())
  df_route = df[cols_route].groupby(cols_route, as_index=False).sum()
  df_route_soon = df_route.copy()
  df_route_late = df_route.copy()
  df_route_soon['time'] = 'soon (6am)'
  df_route_late['time'] = 'late (6pm)'
  col_val_soon = list()
  col_val_late = list()
  for row in df_route.to_dict(orient='records'):
    dur_6am = get_duration(df, row['origem'], row['destino'], 6, cols_duration[i])
    dur_12h = get_duration(df, row['origem'], row['destino'], 12, cols_duration[i])
    dur_6pm = get_duration(df, row['origem'], row['destino'], 18, cols_duration[i])
    soon = (dur_12h - dur_6am) / dur_12h
    late = (dur_6pm - dur_12h) / dur_12h
    col_val_soon.append(soon)
    col_val_late.append(late)
  df_route_soon['diff_perct'] = col_val_soon
  df_route_late['diff_perct'] = col_val_late
  df_comp = pd.concat([df_route_soon, df_route_late])
  df_comp = df_comp.sort_values(cols_route).reset_index(drop=True)
  return df_comp

In [ ]:
# df_comp_traffic = hours_comparison(df_inv, 0)
# df_comp_normal = hours_comparison(df_inv, 1)

### Histograma (tráfego)

`6(a|p)m = 12pm * diff_perct`

In [ ]:
# px.histogram(df_comp_traffic, x='diff_perct', color='time', barmode='overlay', opacity=.5)

### Histograma (normal)

`6(a|p)m = 12pm + 12pm * diff_perct`

In [ ]:
# px.histogram(df_comp_normal, x='diff_perct', color='time', barmode='overlay', opacity=.5)

## Comparação com OSM

### Lendo tabela OSM

In [ ]:
path_dist = get_path('DISTANCIAS', 'distancias.jay')
df_osm = dt.fread(path_dist)
df_osm = df_osm.to_pandas()
df_osm

origem  destino   distancia     tempo
0         110001   110001    0.000000  0.000000
1         110001   110002  309.050000  6.169056
2         110001   110003  399.499700  6.289056
3         110001   110004   81.201103  1.917750
4         110001   110005  391.704300  6.136361
...          ...      ...         ...       ...
31024895  530010   522200  161.728900  2.356000
31024896  530010   522205  382.708800  5.479556
31024897  530010   522220  161.603400  2.248944
31024898  530010   522230  190.000900  3.216083
31024899  530010   530010    0.000000  0.000000

[31024900 rows x 4 columns]

### Mesclando tabelas

Normalizando o tempo entre elas (ambas em segundos).

In [ ]:
df_dist = pd.merge(df_inv, df_osm, how='left', on=['origem', 'destino'])
df_dist['tempo'] = df_dist['tempo'] * 60 * 60
df_dist

KeyboardInterrupt: 

### Coluna da diferença percentual

OSM em relação ao GMAPS.

In [ ]:
reference = ['duration_in_traffic (value)', 'duration (value)']
compare = 'tempo'
df_dist['diff_pct_traffic'] = (df_dist[reference[0]] - df_dist[compare]) / df_dist[compare]
df_dist['diff_pct_normal'] = (df_dist[reference[1]] - df_dist[compare]) / df_dist[compare]
df_dist

status  count    origem   destino  hour     mode traffic_model  \
0            OK    2.0  110001.0  110002.0  18.0  driving   pessimistic   
1            OK   12.0  110001.0  110004.0  18.0  driving   pessimistic   
2            OK    2.0  110001.0  110009.0  18.0  driving   pessimistic   
3            OK   26.0  110001.0  110012.0  18.0  driving   pessimistic   
4            OK    3.0  110001.0  110013.0  18.0  driving   pessimistic   
...         ...    ...       ...       ...   ...      ...           ...   
65933        OK    2.0  530010.0  522200.0  18.0  driving   pessimistic   
65934  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65935  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65936  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   
65937  ApiError    NaN       NaN       NaN   NaN      NaN           NaN   

       distance (value)  duration (value)  duration_in_traffic (value)  \
0              330612.0           18065.0                      20190.0   
1              109937.0            6238.0                       6757.0   
2              143458.0            8228.0                      10193.0   
3              153453.0            8366.0                       9749.0   
4              389010.0           21686.0                      23707.0   
...                 ...               ...                          ...   
65933          163256.0            8350.0                      13232.0   
65934               NaN               NaN                          NaN   
65935               NaN               NaN                          NaN   
65936               NaN               NaN                          NaN   
65937               NaN               NaN                          NaN   

       late_pct   distancia    tempo  diff_pct_traffic  diff_pct_normal  
0      0.117631  309.050000  22208.6         -0.090893        -0.186576  
1      0.083200   81.201103   6903.9         -0.021278        -0.096453  
2      0.238819  145.678200   8445.6          0.206901        -0.025765  
3      0.165312  130.770500   9172.1          0.062897        -0.087886  
4      0.093194  357.511000  25670.4         -0.076485        -0.155214  
...         ...         ...      ...               ...              ...  
65933  0.584671  161.728900   8481.6          0.560083        -0.015516  
65934       NaN         NaN      NaN               NaN              NaN  
65935       NaN         NaN      NaN               NaN              NaN  
65936       NaN         NaN      NaN               NaN              NaN  
65937       NaN         NaN      NaN               NaN              NaN  

[65938 rows x 15 columns]

### Histograma (tráfego)

`gmaps = osm + osm * diff_pct_traffic`

In [ ]:
px.histogram(df_dist, x='diff_pct_traffic')

### Histograma (normal)

`gmaps = osm + osm * diff_pct_normal`

In [ ]:
px.histogram(df_dist, x='diff_pct_normal')

# Exportar tabela

In [ ]:
cols_exp = [
  'origem', 'destino',
  'mode', 'traffic_model', 'hour',
  'distance (value)', 'duration (value)', 'duration_in_traffic (value)'
]

In [ ]:
df_exp = df_inv[cols_exp]
df_exp = df_exp[(
    (df_exp['mode'] == 'driving') & (df_exp['traffic_model'] == 'pessimistic') & (df_exp['hour'] == 18)
  ) | (
    (df_exp['mode'] == 'transit') & (df_exp['traffic_model'] == 'best_guess') & (df_exp['hour'] == 6)
)]
df_exp = df_exp.fillna(0)
df_exp

origem   destino     mode traffic_model  hour  distance (value)  \
0      110001.0  110002.0  driving   pessimistic  18.0          330612.0   
1      110001.0  110004.0  driving   pessimistic  18.0          109937.0   
2      110001.0  110009.0  driving   pessimistic  18.0          143458.0   
3      110001.0  110012.0  driving   pessimistic  18.0          153453.0   
4      110001.0  110013.0  driving   pessimistic  18.0          389010.0   
...         ...       ...      ...           ...   ...               ...   
65929  530010.0  521760.0  driving   pessimistic  18.0           57271.0   
65930  530010.0  521830.0  driving   pessimistic  18.0          311269.0   
65931  530010.0  521975.0  driving   pessimistic  18.0           52771.0   
65932  530010.0  522068.0  driving   pessimistic  18.0          256309.0   
65933  530010.0  522200.0  driving   pessimistic  18.0          163256.0   

       duration (value)  duration_in_traffic (value)  
0               18065.0                      20190.0  
1                6238.0                       6757.0  
2                8228.0                      10193.0  
3                8366.0                       9749.0  
4               21686.0                      23707.0  
...                 ...                          ...  
65929            3323.0                       5523.0  
65930           14915.0                      18021.0  
65931            2800.0                       5182.0  
65932           12146.0                      14996.0  
65933            8350.0                      13232.0  

[60670 rows x 8 columns]

In [ ]:
durations = list()
for dur, dur_trf in zip(df_exp['duration (value)'], df_exp['duration_in_traffic (value)']):
  durations.append(max(dur, dur_trf))
distances = df_exp['distance (value)']

In [ ]:
df_exp = df_exp.loc[:, df_exp.columns[:-3]]
df_exp['duration'] = pd.Series(durations) / 60
df_exp['distance'] = pd.Series(distances) / 1000
df_exp

origem   destino     mode traffic_model  hour    duration  distance
0      110001.0  110002.0  driving   pessimistic  18.0  336.500000   330.612
1      110001.0  110004.0  driving   pessimistic  18.0  112.616667   109.937
2      110001.0  110009.0  driving   pessimistic  18.0  169.883333   143.458
3      110001.0  110012.0  driving   pessimistic  18.0  162.483333   153.453
4      110001.0  110013.0  driving   pessimistic  18.0  395.116667   389.010
...         ...       ...      ...           ...   ...         ...       ...
65929  530010.0  521760.0  driving   pessimistic  18.0         NaN    57.271
65930  530010.0  521830.0  driving   pessimistic  18.0         NaN   311.269
65931  530010.0  521975.0  driving   pessimistic  18.0         NaN    52.771
65932  530010.0  522068.0  driving   pessimistic  18.0         NaN   256.309
65933  530010.0  522200.0  driving   pessimistic  18.0         NaN   163.256

[60670 rows x 7 columns]

In [ ]:
path_exp = get_path('GESTANTES', f'gmaps/route_exp.csv.gzip')
df_exp.to_csv(path_exp, index=False)